In [1]:
from data_processing import load_data, load_tags, filter_movies_with_no_tags, build_index_dictionary, get_movie_vocab
import random
import math
import os
import numpy as np
import tensorflow as tf

In [2]:
# Parameters
batch_size = 128
embedding_size = 200
window_size = 2
neg_samples = 20
learn_rate = 0.1
num_steps = 500001

In [3]:
# Data Loading
print("loading data...")
# train: {userID (string) => list_of_movies}, train_sets: {userID => set(movies)}, test: {userID => next movie}
train, train_sets, test = load_data(validation=False)
# movie_tags: {movieID (str)=>tagId (str), loads tags (if in user-movie combo is in train set), includes genres as tags
movie_tags, vocab = load_tags(train_sets, min_count=2)
print("done")

loading data...
done


In [4]:
train, test = filter_movies_with_no_tags(train, test, movie_tags)
movies_train = list(train.values())
movie_tags_list = list(movie_tags.values())
vocab_size = len(vocab)
num_movies = len(list(movie_tags.keys()))
# avg tags per movie = 17.78249347853091

In [5]:
num_movies

24033

In [16]:
tag_dictionary, tag_reversed_dictionary = build_index_dictionary(vocab)
movie_vocab = movie_tags.keys()
movie_dictionary, movie_reversed_dictionary = build_index_dictionary(list(movie_vocab))

In [18]:
'26018' in movie_vocab

True

In [26]:
graph = tf.Graph()
with graph.as_default():
    a=[]
    b=[]
    for movie,tags in movie_tags.items():
        for tag in tags:
            a.append(movie_dictionary[movie])
            b.append(tag_dictionary[tag])
            
    movie_tags_ragged = tf.RaggedTensor.from_value_rowids(values=b,value_rowids=a)

    print(len(b))
    print(movie_tags_ragged)

406603
tf.RaggedTensor(values=Tensor("RaggedFromValueRowIds/values:0", shape=(406603,), dtype=int32), row_splits=Tensor("RaggedFromValueRowIds/concat:0", shape=(24034,), dtype=int64))


In [21]:
graph = tf.Graph()
with graph.as_default():
    a=[]
    b=[]
    for movie,tags in movie_tags.items():
        for tag in tags:
            a.append(movie_dictionary[movie])
            b.append(tag_dictionary[tag])
            
    movie_tags_ragged = tf.RaggedTensor.from_value_rowids(values=b,value_rowids=a)

    # word input data
    train_word_inputs = tf.placeholder(tf.int32, shape=[batch_size])
    train_word_labels = tf.placeholder(tf.int32, shape=[batch_size, 1])

    # movie input
    train_movie_inputs = tf.placeholder(tf.int32, shape=[batch_size, None])
    train_movie_labels = tf.placeholder(tf.int32, shape=[batch_size, None])

    # embedding layer
    word_embeddings = tf.Variable(tf.random_uniform([vocab_size, embedding_size], -1.0, 1.0))

    # word embeddings
    word_embed = tf.nn.embedding_lookup(word_embeddings, train_word_inputs)

    nce_word_weights = tf.Variable(tf.truncated_normal([vocab_size, embedding_size],
                                                       stddev=1.0 / math.sqrt(embedding_size)))
    nce_word_biases = tf.Variable(tf.zeros([vocab_size]))

    tag_loss = tf.nn.nce_loss(
            weights=nce_word_weights,
            biases=nce_word_biases,
            labels=train_word_labels,
            inputs=word_embed,
            num_sampled=neg_samples,
            num_classes=vocab_size)

    # entering movie loss

    nce_movie_weights = tf.reduce_mean (tf.ragged.map_flat_values (tf.nn.embedding_lookup, nce_word_weights, movie_tags_ragged), 1)

    movie_embed = tf.reduce_mean (tf.ragged.map_flat_values (tf.nn.embedding_lookup, word_embed, movie_tags_ragged), 1)

    nce_movie_biases = tf.Variable(tf.zeros([num_movies]))

    movie_loss = tf.nn.nce_loss(
            weights=nce_movie_weights,
            biases=nce_movie_biases,
            labels=train_movie_labels,
            inputs=movie_embed,
            num_sampled=neg_samples,
            num_classes=num_movies)

    loss = tf.reduce_mean(tag_loss + lambda_hard * movie_loss)

    tf.summary.scalar('loss', loss)

    optimizer = tf.train.GradientDescentOptimizer(learn_rate).minimize(loss)

    norm = tf.sqrt(tf.reduce_sum(tf.square(word_embeddings), 1, keepdims=True))
    normalized_embeddings = word_embeddings / norm

    merged = tf.summary.merge_all()
    init = tf.global_variables_initializer()
    saver = tf.train.Saver()

ValueError: Dimension 0 in both shapes must be equal, but are 128 and 24033. Shapes are [128] and [24033]. for 'nce_loss_1/concat_3' (op: 'ConcatV2') with input shapes: [128,1], [24033,20], [] and with computed input tensors: input[2] = <1>.

In [10]:
movie_tags

{'27866': ['new zealand',
  'amazing ending',
  'boring beginning',
  'annoying',
  'matthew macfadyen',
  'seen 2012',
  'amazing ending',
  'based on a book',
  'divx',
  'journalist',
  'miranda otto',
  'new zealand',
  'nudity (topless)',
  'drama'],
 '48082': ['surreal',
  'unusual',
  'cute',
  'dreamlike',
  'dreams',
  'fanciful',
  'fantasy',
  'love',
  'quirky',
  'romance',
  'stylized',
  'charlotte gainsbourg',
  'dreams',
  'fantasy',
  'mental illness',
  'michel gondry',
  'psychological',
  'psychology',
  'quirky',
  'stylized',
  'surreal',
  'artsy',
  'artsy',
  'bittersweet',
  'charlotte gainsbourg',
  'dream-like',
  'dreams',
  'gael garcã\xada bernal',
  'michel gondry',
  'psychology',
  'quirky',
  'romance',
  'stylized',
  'surreal',
  'dreams',
  'psychology',
  'stylized',
  'surreal',
  'artsy',
  'bittersweet',
  'dream-like',
  'dreams',
  'fantasy',
  'quirky',
  'surreal',
  'pretentious',
  "can't identify with hero",
  'dreams',
  'fantasy',
  '

In [11]:
movie_tags['26018']

['crime', 'film-noir', 'mystery', 'thriller']

In [12]:
movie_dictionary['26018']

KeyError: '26018'